In [244]:
#Data Manipulation
import pandas as pd
import numpy as np

#Plots
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.graph_objects as go
%matplotlib inline
plt.style.use('seaborn-v0_8-darkgrid')

#Utilities
import os
import datetime
import time

#Models
from lightgbm import LGBMRegressor
from xgboost import XGBRegressor
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor, AdaBoostRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from skforecast.ForecasterBaseline import ForecasterEquivalentDate
from skforecast.ForecasterAutoreg import ForecasterAutoreg

#Functionalities
from skforecast.model_selection import backtesting_forecaster
from sklearn.metrics import mean_absolute_error, mean_squared_error

parameters = {
    "dataset":{
        "path": "../data/Processed_Data/Demand_All_Exogenous.csv",
        "trainingSize": .70,
        "validationSize": .15,
        "testSize": .15
    },
    "backtesting":{
        "steps": 96*7,
        "fixedTrainSize": False,
        "refit": False,
    }
}

In [245]:
#Read Dataset {Path Dataset}
df = pd.read_csv(parameters["dataset"]["path"])
df["Date"] = pd.to_datetime(df["Date"])
df.head(5)

Date  Demand  Year  Month  Hour  DayOfWeek  DayOfYear  Day  \
0 2018-01-01 00:15:00       8  2018      1     0          0          1    1   
1 2018-01-01 00:30:00       8  2018      1     0          0          1    1   
2 2018-01-01 00:45:00       8  2018      1     0          0          1    1   
3 2018-01-01 01:00:00       8  2018      1     1          0          1    1   
4 2018-01-01 01:15:00       8  2018      1     1          0          1    1   

   Minute  Temperature  ...  Sunshine_Duration  Shortwave_Radiation  \
0      15    12.967492  ...                0.0                  0.0   
1      30    12.972492  ...                0.0                  0.0   
2      45    12.977492  ...                0.0                  0.0   
3       0    12.982492  ...                0.0                  0.0   
4      15    12.709992  ...                0.0                  0.0   

   Direct_Shortwave_Radiation  Diffuse_Shortwave_Radiation  Demand_7d  \
0                         0.0                          0.0        0.0   
1                         0.0                          0.0        0.0   
2                         0.0                          0.0        0.0   
3                         0.0                          0.0        0.0   
4                         0.0                          0.0        0.0   

   isWeekend  Hour_sen  Hour_cos  Demand_24h  isHoliday  
0      False  0.000000  0.261799           0       True  
1      False  0.000000  0.261799           0       True  
2      False  0.000000  0.261799           0       True  
3      False  0.220297  0.141451           0       True  
4      False  0.220297  0.141451           0       True  

[5 rows x 22 columns]

In [246]:
#Dataset Split
#Podriamos probar otra estrategia para hacer el split
trainingSize = int(parameters["dataset"]["trainingSize"] * df.shape[0])
validationSize = trainingSize + int(parameters["dataset"]["validationSize"] * df.shape[0])
trainingLastDate = str(df.loc[[trainingSize+1]]["Date"].values[0])
validationLastDate = str(df.loc[[validationSize+1]]["Date"].values[0])

x_train = df.loc[:trainingSize, :].copy()
x_val = df.loc[trainingSize + 1: validationSize, :].copy()
x_test = df.loc[validationSize + 1:, :].copy()

df = df.set_index("Date")
df = df.asfreq("15min")
x_train = x_train.set_index("Date")
x_train = x_train.asfreq("15min")
x_val = x_val.set_index("Date")
x_val = x_val.asfreq("15min")
x_test = x_test.set_index("Date")
x_test = x_test.asfreq("15min")

print(f"Whole Dataset Size: {df.shape[0]}")
print(f"Trainig Dataset Size: {x_train.shape[0]} From: {x_train.index.min()} to {x_train.index.max()}")
print(f"Validation Dataset Size: {x_val.shape[0]} From: {x_val.index.min()} to {x_val.index.max()}")
print(f"Test Dataset Size: {x_test.shape[0]} From: {x_test.index.min()} to {x_test.index.max()}")

print(trainingLastDate)
print(validationLastDate)

Whole Dataset Size: 70080
Trainig Dataset Size: 49057 From: 2018-01-01 00:15:00 to 2019-05-27 00:15:00
Validation Dataset Size: 10512 From: 2019-05-27 00:30:00 to 2019-09-13 12:15:00
Test Dataset Size: 10511 From: 2019-09-13 12:30:00 to 2020-01-01 00:00:00
2019-05-27T00:30:00.000000000
2019-09-13T12:30:00.000000000


In [247]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=x_train.index, y=x_train["Demand"], mode="lines", name="Train"))
fig.add_trace(go.Scatter(x=x_val.index, y=x_val["Demand"], mode="lines", name="Validation"))
fig.add_trace(go.Scatter(x=x_test.index, y=x_test["Demand"], mode="lines", name="Test"))
fig.update_layout(
    title = "Dataset Partition",
    xaxis_title = "Date",
    yaxis_title ="Demand (MWh)",
    width = 1000,
    height = 400,
    margin = dict(l=30, r=20, t=35, b=60),
    legend = dict(
        orientation = "h",
        yanchor = "bottom",
        y = 1.05,
        xanchor = "right",
        x=1
    )
)
fig.show()

In [248]:
#Equivalent Date (Baseline Model)
baselineForecaster = ForecasterEquivalentDate(
    offset= pd.DateOffset(weeks=1),
    n_offsets=2,
    agg_func=np.mean
)
baselineForecaster.fit(y=x_train["Demand"])
print(len(x_val) + len(x_test))
predictions = baselineForecaster.predict(steps = 21023)
predictions = predictions.to_frame()


21023


In [249]:
def plotPredictions(preds, tests):
    fig = go.Figure()
    trace1 = go.Scatter(x=tests.index, y=tests["Demand"], name="test", mode="lines")
    trace2 = go.Scatter(x=preds.index, y=preds["pred"], name="predictions", mode="lines")
    fig.add_trace(trace1)
    fig.add_trace(trace2)
    fig.update_layout(
        title="Real value vs Predicted in Test Data",
        xaxis_title="Date Time",
        yaxis_title="Demand",
        width=1020,
        height=450,
        margin = dict(l=70, r=20, t=55, b=20),
        legend = dict(
            orientation = "h",
            yanchor="top",
            y=1.1,
            xanchor="left",
            x=0.76
        )
    )
    fig.show()

In [250]:
#EquivalentDate Algorithm Results 1 Week
#test_dates = df.loc[(df.index > x_val.index.min()) & (df.index <= x_val.index.min()+datetime.timedelta(weeks=1))]

print(f"MAE: {mean_absolute_error(df[trainingLastDate:].Demand.values, predictions.pred.values)}, MSE: {mean_squared_error(df[trainingLastDate:].Demand.values, predictions.pred.values)}")
plotPredictions(preds=predictions, tests=df[trainingLastDate:])

MAE: 22.59277933691671, MSE: 1408.7759120962755


In [251]:
def run_backtesting(model, data, initial_train_size, params, exog=None):
    init = time.time()
    forecaster = ForecasterAutoreg(
        regressor = model,
        transformer_y = StandardScaler(),
        lags=24*7
    )
    #forecaster.fit(y=data["Demand"], exog=exog)
    metrics, predictions = backtesting_forecaster(
        forecaster = forecaster,
        steps = params["backtesting"]["steps"],
        y = data["Demand"],
        metric = ['mean_absolute_error', 'mean_squared_error'],
        exog = exog,
        initial_train_size = initial_train_size,
        refit = params["backtesting"]["refit"],
        fixed_train_size = parameters["backtesting"]["fixedTrainSize"],
        verbose = False,
        show_progress = True,
        n_jobs='auto'
    )
    end = time.time()
    return predictions, metrics, (end-init)

In [252]:
models = {
    'LGBM': LGBMRegressor(n_estimators=100, random_state=123, verbose=-1),
    'XGBoost': XGBRegressor(n_estimators=100, random_state=123),
    'KNNR': KNeighborsRegressor(n_neighbors=5, weights='distance'),
    "SVR": SVR(kernel='rbf'),
    'GBM': GradientBoostingRegressor(n_estimators=100, random_state=123),
    'RF': RandomForestRegressor(n_estimators=100, random_state=123),
    'ADA': AdaBoostRegressor(n_estimators=100, random_state=123)
}
results = {}
for model_name, model in models.items():
    predictions, metrics, model_time = run_backtesting(model, df, len(x_train)+len(x_val), parameters)
    results[model_name] = {
        'predictions': predictions,
        'MAE': metrics[0],
        'MSE': metrics[1],
        'Time': model_time
    }
    print(f"Model {model_name}: MAE: {metrics[0]}, MSE: {metrics[1]}, Time: {model_time:.6f} seconds")

100%|██████████| 110/110 [00:11<00:00,  9.77it/s]


Model LGBM: MAE: 14.111483399634476, MSE: 785.6796252308189, Time: 14.675228 seconds


100%|██████████| 110/110 [00:05<00:00, 18.81it/s]


Model XGBoost: MAE: 18.18031971427641, MSE: 1265.9039182261358, Time: 8.716879 seconds


100%|██████████| 110/110 [01:16<00:00,  1.43it/s]


...

Model GBM: MAE: 16.667842618998343, MSE: 833.3937749356201, Time: 102.331918 seconds


100%|██████████| 110/110 [00:26<00:00,  4.09it/s]


Model RF: MAE: 15.95058510132242, MSE: 1062.9544891256776, Time: 742.371333 seconds


100%|██████████| 110/110 [00:58<00:00,  1.87it/s]

Model ADA: MAE: 53.36502030791121, MSE: 3566.253967804828, Time: 133.704982 seconds


### Hyperparameter Tuning

In [259]:
from skforecast.model_selection import grid_search_forecaster

#Lags used as Predictors
lags_grid = [[96], [24*7], [96*7]]

#Regressor Hyperparameters
param_grid = {
    'n_neighbors': [5, 10],
    'weights': ['uniform', 'distance'],
    'algorithm': ['auto', 'ball_tree', 'kd_tree', 'brute']
}

forecaster = ForecasterAutoreg(
    regressor = KNeighborsRegressor(n_neighbors=5, weights= 'distance'),
    transformer_y = StandardScaler(),
    lags=24*7
)

results = grid_search_forecaster(
    forecaster = forecaster,
    y = df['Demand'],
    param_grid = param_grid,
    steps = 96,
    lags_grid = lags_grid,
    refit = parameters["backtesting"]["refit"],
    metric = ["mean_squared_error", 'mean_absolute_error'],
    initial_train_size = len(x_train) + len(x_val),
    n_jobs = 'auto',
    verbose = False,
    show_progress=True,
    return_best = True,
    fixed_train_size=parameters['backtesting']["fixedTrainSize"]
)

Number of models compared: 48.


lags grid:   0%|          | 0/3 [00:35<?, ?it/s]


KeyboardInterrupt: 

In [ ]:
#Best Forecaster
forecaster